In [1]:
import requests
import os
from dotenv import load_dotenv
import json
import pandas as pd
import pymysql
import numpy as np
from tqdm import tqdm

In [2]:
load_dotenv()

True

In [3]:
#Loading constants
GEO_LOCATION_API_KEY = os.getenv('GEOLOCATION_API_KEY')
DB_HOST = os.getenv('HOSTNAME')
DB_USER = os.getenv('HOST')
DB_PASSWORD = os.getenv('PASSWORD')
DB_NAME = os.getenv('DB_NAME')

## REQUESTING API

In [4]:
def request_given_lat_lon(lat:float, lon:float) -> dict:
    '''
    Request geolocation api given a latitude and longitude
    '''
    url = f'https://api.tomtom.com/search/2/poiSearch/restaurant.json?key={GEO_LOCATION_API_KEY}&limit=100&lat={lat}&lon={lon}&radius=1000'
    response = requests.get(url)
    decoded_response = json.loads(response.content)
    return decoded_response['results']

In [6]:
#Creating arrays for requested area lat and lon
lat, lon = -23.697907, -46.828054
final_lat, final_lon = -23.506020, -46.419272

lat_range = np.arange(lat, final_lat, 0.01)
lon_range = np.arange(lon, final_lon, 0.01)


In [7]:
lat_range.shape[0]

20

In [8]:
lon_range.shape[0]

41

In [9]:
restaurant_list = []

for la in tqdm(range(len(lat_range))):
    for lo in lon_range:
        restaurant_list.extend(request_given_lat_lon(lat_range[la], lo))

100%|██████████| 20/20 [08:16<00:00, 24.81s/it]


In [10]:
restaurant_info = {
    'name' : [],
    'lat' : [],
    'lon' : [] ,
    'street_name' : [],
    'neighborhood': []
}


In [ ]:

for restaurant in restaurant_list:
    #checks if the response has the desisred info
    if 'name' in restaurant['poi'] and 'lat' in restaurant['position'] and\
         'lon' in restaurant['position'] and 'streetName' in restaurant['address'] and\
         'municipalitySubdivision' in restaurant['address']:
        restaurant_info['name'].append(restaurant['poi']['name'])
        restaurant_info['lat'].append(restaurant['position']['lat'])
        restaurant_info['lon'].append(restaurant['position']['lon'])
        restaurant_info['street_name'].append(restaurant['address']['streetName'])
        restaurant_info['neighborhood'].append(restaurant['address']['municipalitySubdivision'])
    

In [11]:
df = pd.DataFrame(restaurant_info)

In [13]:
df = df.drop_duplicates()

In [14]:
df.head()

name       lat       lon             street_name  \
0                      Rosa Lala -23.69465 -46.80349            Rua Eldorado   
1                  Maxi Salgados -23.70367 -46.80641           Rua Palestina   
2                    Pão da Vila -23.70410 -46.80325  Avenida Getúlio Vargas   
3  Bar e Mercearia São Francisco -23.70417 -46.80326  Avenida Getúlio Vargas   
4              Bar Dismantelados -23.70542 -46.80563  Rua Deodoro da Fonseca   

          neighborhood  
0  Chácara Santa Maria  
1  Chácara Santa Maria  
2  Chácara Santa Maria  
3  Chácara Santa Maria  
4  Chácara Santa Maria

In [55]:
df.shape

(57261, 5)

In [ ]:
df.info()

In [ ]:
df.to_csv('restaurants_data.csv', encoding='utf-8')

## SQL WRITING

In [47]:

connection = pymysql.connect(
    host=DB_HOST,
    user=DB_USER,
    password=DB_PASSWORD,
    db=DB_NAME
)

In [48]:
cursor = pymysql.cursors.Cursor(connection)

In [51]:
#Executing query function
def commit_values(values:str, cursor:pymysql.cursors.Cursor) -> None:
    '''
    Commits a insertion query 
    '''
    BEGINNING = 'INSERT INTO restaurants VALUES '
    query = BEGINNING + values[:-3] + ';' 
    cursor.execute(query)
    connection.commit()

In [52]:
#Creating query and executing 
query = ''
for index, row in df.iterrows():
    query += f'''(NULL, "{row['name']}", {row['lat']}, {row['lon']}, "{row['street_name']}", "{row['neighborhood']}"), \n'''
    if index%500==0:
        commit_values(query, cursor)
        query = ''

commit_values(query, cursor)

In [30]:
print(query)

INSERT INTO restaurants VALUES (NULL, "Rosa Lala", -23.69465, -46.80349, "Rua Eldorado", "Chácara Santa Maria"), 
(NULL, "Maxi Salgados", -23.70367, -46.80641, "Rua Palestina", "Chácara Santa Maria"), 
(NULL, "Pão da Vila", -23.7041, -46.80325, "Avenida Getúlio Vargas", "Chácara Santa Maria"), 
(NULL, "Bar e Mercearia São Francisco", -23.70417, -46.80326, "Avenida Getúlio Vargas", "Chácara Santa Maria"), 
(NULL, "Bar Dismantelados", -23.70542, -46.80563, "Rua Deodoro da Fonseca", "Chácara Santa Maria"), 
(NULL, "Biroska da Dindinha", -23.70493, -46.80389, "Rua Deodoro da Fonseca", "Chácara Santa Maria"), 
(NULL, "Lanchonete da Melry", -23.7053, -46.80464, "Rua Hermes da Fonseca", "Chácara Santa Maria"), 
(NULL, "Buffet Puro Sabor", -23.69314, -46.80074, "Rua Foz do Iguaçu", "Chácara Santa Maria"), 
(NULL, "Pizzaria e Esfiharia Bob", -23.69288, -46.80086, "Rua Foz do Iguaçu", "Chácara Santa Maria"), 
(NULL, "Bar do Chaves", -23.70579, -46.80496, "Rua Hermes da Fonseca", "Chácara Santa M

In [43]:
connection.close()